# Bad Electrodes

Here, we simply want to plot the different bad electrodes as found by Nicolas and as found by me. Each of these will be plotted next to some normal/good electrodes (both agreed upon) and will look for jumps in noise/weird behavior.

In addition, will plot spectograms of bad electrodes, as these may be off as well.
***
## Code for plots

In [14]:
from plotly.offline import download_plotlyjs, init_notebook_mode, iplot, plot
from plotly.graph_objs import *
from plotly import tools
init_notebook_mode()
import pandas as pd

In [6]:
# data should be inputted list of tuples:
# spot 0 = voltage, spot 1 = electrode number
def get_time_plot(title, time, eeg_data, elecs):
    # first set data
    plot_data = []
    for elec in elecs:
        plot_data.append(Scatter(
            x = time[550:8000, 0],
            y = eeg_data[550:8000, elec],
            name = 'Electrode ' + str(elec)
        ))

    # Setup layout

    layout = dict(title = title + ' Voltage vs Time',
                  xaxis = dict(title = 'Time(1/500th of a second)'),
                  yaxis = dict(title = 'Voltage(mV)'),
                  )

    # Make figure object
    fig = dict(data=plot_data, layout=layout)
    
    iplot(fig)

In [7]:
import numpy as np
from scipy.signal import spectrogram

In [19]:
# data should be inputted list of tuples:
# spot 0 = voltage, spot 1 = electrode number
def get_freq_plot(title, time, eeg_data, elecs):
    
    f, t, Sxx = spectrogram(eeg_data, 500)
    print Sxx.shape
    sp = pd.DataFrame(data=np.log(Sxx[:,:,0].T), index = t, columns = f)
    fig = sp.iplot(kind='heatmap', colorscale='spectral', asFigure=True,
        title="Spectrogram for " + str(cols[ind]), theme='solar',
        xTitle='Time', yTitle = 'Frequency', zTitle="log magnitude")
    fig.data.update(dict(colorbar=dict(title="Magnitude logscale", titleside="right")))
    iplot(fig)
    
#     first set data
#     freqs = np.fft.fftfreq(int(time[8000,0]/500), 500)
#     plot_data = []
#     print "Time done"
#     for elec in elecs:
# #         ps = np.abs(np.fft.fft(eeg_data[0:8000, elec]))**2
#         plot_data.append(Scatter(
#             x = freqs,
#             y = ps,
#             name = 'Electrode ' + str(elec)
#         ))


    # Setup layout

#     layout = dict(title = title + ' Freq Plot',
#                   xaxis = dict(title = 'Freq(Wave/Sec)'),
#                   yaxis = dict(title = 'Amplitude'),
#                   )

#     # Make figure object

#     fig = dict(data=plot_data, layout=layout)
    
#     return iplot(fig)

***
## Read in the data from Patient Files

In [9]:
import h5py
import os
os.chdir("C:/Users/Nitin/Documents/Hopkins/BCI/datashare")

# return tuple of patient info
def get_patient(filename, nitin_bad, zero_elec):
    D = h5py.File(filename, 'r')
    patient = D["result"]["data"][:, :]
    time = D["result"]["times"][:]
    nic_bad = D["result"]["auto_badchans"][:]
    # make it 0-indexed
    nic_bad = [int(x) - 1 for x in nic_bad]
    nitin_bad = [int(x) - 1 for x in nitin_bad]
    zero_elec = [int(x) - 1 for x in zero_elec]
    # get good electrodes
    elec_range = range(0, 110)
    good_elec = set(elec_range).difference(nic_bad).difference(nitin_bad).difference(zero_elec)
    return patient, time, nic_bad, nitin_bad, zero_elec, good_elec

# First do A00051826_01
# add my bad electrodes
patient0_01_nitin_bad = [52, 58, 72, 78, 79, 95, 100, 105, 111]
patient0_01_zero = [1, 8, 14, 20, 24, 31]
# get obj
patient0_01 = get_patient("full_A00051826_01.mat", patient0_01_nitin_bad, patient0_01_zero)


# then test.mat
patient1_nitin_bad = [52, 58, 72, 73, 78, 79]
patient1_zero = [1, 8, 20, 24, 31]
patient1 = get_patient("test.mat", patient1_nitin_bad, patient1_zero)

***
## Plot Data
With these 2 datasets, let's tinker with what plots are best to use. Then we might be able to add more.

In [10]:
# set random seed
np.random.seed(123)

In [11]:
# First patient0_01
patient0_01_good_elec = np.random.choice(np.array(list(patient0_01[5])), 5)
patient1_good_elec = np.random.choice(np.array(list(patient1[5])), 5)

In [12]:
to_plot = [patient0_01_good_elec, patient0_01[2], patient0_01[3]]
titles = ["Good Electrodes", "Nicolas's Bad Electrodes", "Nitin's Bad Electrodes"]
#print to_plot[0]
#get_time_plot(titles[0], patient0_01[1], patient0_01[0], to_plot[0])

for i in range(3):
     get_time_plot(titles[i], patient0_01[1], patient0_01[0], to_plot[i])

In [20]:
# for i in range(3):
#      get_freq_plot(titles[i], patient0_01[1], patient0_01[0], to_plot[i])
get_freq_plot(titles[0], patient0_01[1], patient0_01[0], 0)

(209026L, 56L, 1L)


ValueError: Shape of passed values is (209026, 56), indices imply (56, 1)